In [69]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib
matplotlib.rcParams["figure.figsize"]=(20,10)
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')

In [70]:
import torch 
import torch.nn as nn

In [71]:
df=pd.read_csv('iris.csv')

In [72]:
df.columns=['x1','x2','x3','x4','y']
df

x1   x2   x3   x4  y
0    5.1  3.5  1.4  0.2  0
1    4.9  3.0  1.4  0.2  0
2    4.7  3.2  1.3  0.2  0
3    4.6  3.1  1.5  0.2  0
4    5.0  3.6  1.4  0.2  0
..   ...  ...  ...  ... ..
145  6.7  3.0  5.2  2.3  2
146  6.3  2.5  5.0  1.9  2
147  6.5  3.0  5.2  2.0  2
148  6.2  3.4  5.4  2.3  2
149  5.9  3.0  5.1  1.8  2

[150 rows x 5 columns]

In [73]:
x=df[['x1','x2','x3','x4']]
y=df['y']

In [74]:
y=pd.get_dummies(y)
y

0  1  2
0    1  0  0
1    1  0  0
2    1  0  0
3    1  0  0
4    1  0  0
..  .. .. ..
145  0  0  1
146  0  0  1
147  0  0  1
148  0  0  1
149  0  0  1

[150 rows x 3 columns]

In [75]:
x=torch.from_numpy(x.values).type(torch.float)
y=torch.from_numpy(y.values).type(torch.float)

In [76]:
torch.argmax(y,axis=1)

tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2])

In [77]:
from sklearn.model_selection import train_test_split

In [78]:
X_train,X_test,y_train,y_test=train_test_split(x,y,stratify=y,random_state=0)

In [79]:
def accuracyfunction(ypred,ytest):
    right=(torch.argmax(ypred,axis=1)==torch.argmax(ytest,axis=1)).sum()
    acc=right*100/len(ypred)
    return acc.item()

In [80]:
a=np.array([[1,0,0],[0,0,1]])

In [81]:
b=np.array([[2,1,0],[1,0,0]])

In [82]:
a=torch.from_numpy(a).type(torch.float)
b=torch.from_numpy(b).type(torch.float)

In [83]:
accuracyfunction(a,b)

50.0

# Training the model

In [84]:
class Model(nn.Module):
    def __init__(self):
        super().__init__()
        self.layer1=nn.Linear(4,5)
        self.layer2=nn.ReLU()
        self.layer3=nn.Linear(5,3)
    
    def forward(self,x):
        return self.layer3(self.layer2(self.layer1(x)))    

In [85]:
model=Model()

In [86]:
list(model.named_parameters())

[('layer1.weight',
  Parameter containing:
  tensor([[-0.3799,  0.1191, -0.2621,  0.0682],
          [ 0.3971,  0.0574,  0.4232,  0.4165],
          [-0.2150, -0.1946,  0.3499,  0.1196],
          [ 0.4875, -0.3001, -0.1961,  0.1316],
          [-0.3703,  0.2611,  0.2984,  0.2682]], requires_grad=True)),
 ('layer1.bias',
  Parameter containing:
  tensor([-0.1438,  0.1890, -0.1560,  0.2666, -0.4958], requires_grad=True)),
 ('layer3.weight',
  Parameter containing:
  tensor([[-0.1558,  0.3617, -0.0349, -0.4438, -0.3202],
          [ 0.2460,  0.1671, -0.3508,  0.0731,  0.0587],
          [ 0.3318, -0.1849,  0.2581,  0.2102, -0.1699]], requires_grad=True)),
 ('layer3.bias',
  Parameter containing:
  tensor([ 0.0444, -0.1171,  0.2379], requires_grad=True))]

In [87]:
lossfn=nn.CrossEntropyLoss()
optimizer=torch.optim.Adam(params=model.parameters(),lr=0.001)

In [88]:
epochs=10000
trainingloss=[]
testloss=[]
trainingacc=[]
testacc=[]
params=[]
optparams=[]
for epoch in range(epochs):
    ypred=model(X_train)
    loss=lossfn(ypred,y_train)
    accuracy=accuracyfunction(ypred,y_train)
    trainingloss.append(loss)
    trainingacc.append(accuracy)
    params.append(list(model.named_parameters()))
    optparams.append(optimizer.__dict__)
    loss.backward()
    optimizer.step()
    optimizer.zero_grad()
    if epoch%10==0:
        ypredtest=model(X_test)
        acctest=accuracyfunction(ypredtest,y_test)
        testacc.append(acctest)
        

In [89]:
trainingacc

[24.10714340209961,
 24.10714340209961,
 17.85714340209961,
 17.85714340209961,
 16.071428298950195,
 12.5,
 10.714285850524902,
 8.928571701049805,
 8.928571701049805,
 7.142857074737549,
 5.357142925262451,
 4.464285850524902,
 3.5714285373687744,
 3.5714285373687744,
 2.6785714626312256,
 2.6785714626312256,
 2.6785714626312256,
 4.464285850524902,
 5.357142925262451,
 4.464285850524902,
 3.5714285373687744,
 3.5714285373687744,
 6.25,
 8.035714149475098,
 8.928571701049805,
 10.714285850524902,
 15.178571701049805,
 16.964284896850586,
 18.75,
 20.535715103149414,
 21.428571701049805,
 25.0,
 26.785715103149414,
 29.464284896850586,
 30.35714340209961,
 31.25,
 31.25,
 31.25,
 32.14285659790039,
 33.03571319580078,
 33.03571319580078,
 33.03571319580078,
 33.03571319580078,
 33.92856979370117,
 34.82143020629883,
 34.82143020629883,
 39.28571319580078,
 40.17856979370117,
 40.17856979370117,
 43.75,
 47.32143020629883,
 48.21428680419922,
 47.32143020629883,
 43.75,
 44.64285659790

In [90]:
testacc

[21.052631378173828,
 0.0,
 0.0,
 28.947368621826172,
 34.21052551269531,
 44.73684310913086,
 44.73684310913086,
 34.21052551269531,
 34.21052551269531,
 34.21052551269531,
 34.21052551269531,
 52.6315803527832,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 65.78947448730469,
 68.42105102539062,
 68.42105102539062,
 68.42105102539062,
 71.0526351928711,
 71.0526351928711,
 71.0526351928711,
 71.0526351928711,
 73.68421173095703,
 76.31578826904297,
 76.31578826904297,
 76.31578826904297,
 78.9473648071289,
 81.57894897460938,
 81.57894897460938,
 86.84210205078125,
 86.84210205078125,
 86.84210205078125,
 86.84210205078125,
 86.84210205078125,
 89.47368621826172,
 92.10526275634766,
 94.7368392944336,
 94.736839294

In [91]:
params

[[('layer1.weight',
   Parameter containing:
   tensor([[-0.3799,  0.1191, -0.2621,  0.0682],
           [ 1.2551,  1.3046,  0.0647, -0.4571],
           [-0.0604, -0.6661,  1.0323,  1.8646],
           [ 0.2280, -1.1660,  0.8905,  1.1240],
           [ 0.4487, -0.2130,  1.4941,  1.8937]], requires_grad=True)),
  ('layer1.bias',
   Parameter containing:
   tensor([-0.1438,  2.7959, -4.6602,  0.9351, -4.0403], requires_grad=True)),
  ('layer3.weight',
   Parameter containing:
   tensor([[-0.1558,  1.2579, -0.7400, -1.8620, -2.0113],
           [ 0.2460,  0.2515, -3.8313,  2.4923, -0.9789],
           [ 0.3318, -0.9929,  2.7928,  0.3612,  1.7542]], requires_grad=True)),
  ('layer3.bias',
   Parameter containing:
   tensor([ 0.8555,  2.4138, -1.2847], requires_grad=True))],
 [('layer1.weight',
   Parameter containing:
   tensor([[-0.3799,  0.1191, -0.2621,  0.0682],
           [ 1.2551,  1.3046,  0.0647, -0.4571],
           [-0.0604, -0.6661,  1.0323,  1.8646],
           [ 0.2280, -1.16

In [92]:
l=[]
for i in params:
    #print(i)
    t=[]
    for j in i:
        #print(j)
        for k in j[1]:
            #print(k)
            k=k.detach().numpy()
            t.extend(k.flatten())
    t=tuple(t)        
    l.append(t)
            
            
    

In [93]:
paramvalues=pd.DataFrame(l)

In [94]:
paramvalues

0         1        2         3         4         5         6   \
0    -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
1    -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
2    -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
3    -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
4    -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
...        ...       ...      ...       ...       ...       ...       ...   
9995 -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
9996 -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
9997 -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
9998 -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   
9999 -0.379878  0.119058 -0.26208  0.068202  1.255092  1.304617  0.064711   

            7         8         9   ...        33        34        35  \
0    -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
1    -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
2    -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
3    -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
4    -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
...        ...       ...       ...  ...       ...       ...       ...   
9995 -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
9996 -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
9997 -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
9998 -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   
9999 -0.457145 -0.060352 -0.666123  ...  2.492296 -0.978909  0.331785   

            36        37       38       39        40        41        42  
0    -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
1    -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
2    -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
3    -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
4    -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
...        ...       ...      ...      ...       ...       ...       ...  
9995 -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
9996 -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
9997 -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
9998 -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  
9999 -0.992872  2.792798  0.36117  1.75415  0.855491  2.413799 -1.284733  

[10000 rows x 43 columns]

In [95]:
optparams

[{'defaults': {'lr': 0.001,
   'betas': (0.9, 0.999),
   'eps': 1e-08,
   'weight_decay': 0,
   'amsgrad': False,
   'maximize': False,
   'foreach': None,
   'capturable': False},
  '_zero_grad_profile_name': 'Optimizer.zero_grad#Adam.zero_grad',
  'state': defaultdict(dict,
              {Parameter containing:
               tensor([[-0.3799,  0.1191, -0.2621,  0.0682],
                       [ 1.2551,  1.3046,  0.0647, -0.4571],
                       [-0.0604, -0.6661,  1.0323,  1.8646],
                       [ 0.2280, -1.1660,  0.8905,  1.1240],
                       [ 0.4487, -0.2130,  1.4941,  1.8937]], requires_grad=True): {'step': tensor(10000.),
                'exp_avg': tensor([[ 0.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00],
                        [-5.2190e-05, -3.2352e-05, -9.5042e-06, -4.9938e-07],
                        [ 1.4937e-04,  8.3482e-05,  1.0134e-04,  3.4820e-05],
                        [-3.6629e-05, -7.5635e-06, -1.2360e-04, -5.1048e-05],
           

In [97]:
optparams[0]['param_groups']

[{'params': [Parameter containing:
   tensor([[-0.3799,  0.1191, -0.2621,  0.0682],
           [ 1.2551,  1.3046,  0.0647, -0.4571],
           [-0.0604, -0.6661,  1.0323,  1.8646],
           [ 0.2280, -1.1660,  0.8905,  1.1240],
           [ 0.4487, -0.2130,  1.4941,  1.8937]], requires_grad=True),
   Parameter containing:
   tensor([-0.1438,  2.7959, -4.6602,  0.9351, -4.0403], requires_grad=True),
   Parameter containing:
   tensor([[-0.1558,  1.2579, -0.7400, -1.8620, -2.0113],
           [ 0.2460,  0.2515, -3.8313,  2.4923, -0.9789],
           [ 0.3318, -0.9929,  2.7928,  0.3612,  1.7542]], requires_grad=True),
   Parameter containing:
   tensor([ 0.8555,  2.4138, -1.2847], requires_grad=True)],
  'lr': 0.001,
  'betas': (0.9, 0.999),
  'eps': 1e-08,
  'weight_decay': 0,
  'amsgrad': False,
  'maximize': False,
  'foreach': None,
  'capturable': False}]